In [14]:
%matplotlib inline
%config InlineBackend.figure_format = 'retina'

In [15]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from bilby.gw.result import CBCResult

In [16]:
rng = np.random.default_rng(12345)

sns.set_theme(palette='colorblind', font_scale=1.5)

plt.rcParams.update({
    "text.usetex": True,
    "font.family": "serif",
    "font.serif": ["Computer Modern Roman"],
})

nsamples = 3000

In [17]:
n_dim_unlensed = 11

chains_unlensed = np.load('/Users/ckng419/Termius/GW150914.npz')['chains']

samples_all_unlensed = chains_unlensed.reshape(-1,n_dim_unlensed)

labels_unlensed = ['$M_c$', '$q$', '$\chi_1$', '$\chi_2$', '$d_L$', '$t_c$', '$\phi_c$', '$\cos\iota$', '$\psi$', '$RA$', '$\sin({DEC})$']

df_unlensed = pd.DataFrame()
for i in range(11):
    df_unlensed[labels_unlensed[i]] = samples_all_unlensed[:,i]
    
df_unlensed = df_unlensed.sample(n=nsamples, random_state=rng)
    
df_unlensed['lensed'] = np.full(len(df_unlensed), "unlensed")

In [18]:
n_dim_lensed = 15

chains_lensed = np.load('/Users/ckng419/Termius/GW150914_two_images.npz')['chains']

samples_all_lensed = chains_lensed.reshape(-1,n_dim_lensed)

labels_lensed = ['$M_c$', '$q$', '$\chi_1$', '$\chi_2$', '$d_L$', '$t_c$', '$\phi_c$', '$\cos\iota$', '$\psi$', '$RA$', '$\sin({DEC})$',
          '$d_{L2}$', '$t_2$', '$n_1$', '$n_2$'
          ]

df_lensed = pd.DataFrame()
for i in range(n_dim_lensed):
    df_lensed[labels_lensed[i]] = samples_all_lensed[:,i]
    
df_lensed = df_lensed.sample(n=nsamples, random_state=rng)

for i in [0, 0.5, 1]:
    mask1 = (df_lensed['$n_1$'] >= i) & (df_lensed['$n_1$'] < i + 0.5)
    df_lensed.loc[mask1, '$n_1$'] = i
    mask2 = (df_lensed['$n_2$'] >= i) & (df_lensed['$n_2$'] < i + 0.5)
    df_lensed.loc[mask2, '$n_2$'] = i
    
df_lensed['lensed'] = np.full(len(df_lensed), "lensed")

In [19]:
df = pd.concat([df_unlensed, df_lensed], ignore_index=True)

In [22]:
g = sns.pairplot(df,
                 hue='lensed',
                 corner=True, kind='kde', diag_kind='hist',
                 diag_kws=dict(common_norm=False, rasterized=True),
                 plot_kws=dict(common_norm=False, levels=[0.90,0.3935]))

KeyboardInterrupt: 

In [ ]:
result_GR = CBCResult.from_json("/Users/ckng419/Downloads/birefringence/GW150914_GR.json.gz").posterior
result_GR['cos_iota'] = np.cos([float(value) for value in result_GR['iota']])

trigger_time = 1126259462.4

true_param = np.array([result_GR['chirp_mass'].median(),
                       result_GR['mass_ratio'].median(),
                       result_GR['a_1'].median(),
                       result_GR['a_2'].median(),
                       result_GR['luminosity_distance'].median(),
                       result_GR['geocent_time'].median() - trigger_time,
                       result_GR['phase'].median(),
                       result_GR['cos_iota'].median(),
                       result_GR['psi'].median(),
                       result_GR['ra'].median(),
                       np.sin(result_GR['dec']).median()])

for i in range(n_dim):
    g.axes[i,i].axvline(true_param[i], color=sns.color_palette()[3])
    for j in range(i):
        g.axes[i,j].axvline(true_param[j], color=sns.color_palette()[3])
        g.axes[i,j].axhline(true_param[i], color=sns.color_palette()[3])